In [ ]:
!pip install antspyx
! pip install pydicom nibabel dicom2nifti

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 22.2/22.2 MB 48.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 64.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.1/13.1 MB 81.5 MB/s eta 0:00:00


In [ ]:
import ants
import matplotlib.pyplot as plt
import numpy as np
import pydicom
import nibabel as nib
import dicom2nifti
import os

In [ ]:
from google.colab import drive

# Unmount the drive first
drive.flush_and_unmount()
print('Drive unmounted')

   # Now mount it again
drive.mount('/content/Shareddrive')

Drive not mounted, so nothing to flush and unmount.
Drive unmounted
Mounted at /content/Shareddrive


In [ ]:
def loading_ims(img, template= "MNI152_T1_1mm.nii", brain_mask=  "MNI152_T1_1mm_Brain_Mask.nii"):
    mri_image = ants.image_read(img, reorient='IAL')
    template_image = ants.image_read(template, reorient='IAL')
    brain_mask = ants.image_read(brain_mask, reorient='IAL')

    img_MRI_resampled = ants.resample_image(mri_image, (1, 1, 1.2), False, 4)
    img_template_resampled = ants.resample_image(template_image, (1, 1, 1.2), False, 4)
    return img_MRI_resampled, img_template_resampled, brain_mask

def regestration(img_MRI_resampled, img_template_resampled):
    affine_registration = ants.registration(fixed=img_template_resampled, moving=img_MRI_resampled, type_of_transform="Affine")
    img_MRI_resampled_aligned = affine_registration['warpedmovout']
    registration = ants.registration(fixed=img_template_resampled, moving=img_MRI_resampled_aligned, type_of_transform="SyN")
    aligned_image = registration['warpedmovout']
    return aligned_image

def brain_masking(aligned_image, brain_mask):
    brain_mask = ants.resample_image_to_target(brain_mask, aligned_image)
    brain_only_image = aligned_image * brain_mask
    return brain_only_image

def winsorizing_biasfield(brain_only_image):
    winsorized = ants.iMath(brain_only_image, "TruncateIntensity", 0.05, 0.95)
    n4_corrected_image = ants.n4_bias_field_correction(winsorized)
    return n4_corrected_image

# Step 5: Normalization
def normalize_image(img):
    img_array = img.numpy()
    normalized_array = (img_array - np.min(img_array)) / (np.max(img_array) - np.min(img_array))
    normalized_image = ants.from_numpy(normalized_array, spacing=img.spacing)
    return normalized_image

# Step 6: Downsampling
def downsample_image(img):
    downsampled_image = ants.resample_image(img, (64,64,64), use_voxels=True)
    return downsampled_image

# Function to visualize one slice from each plane
def visualization(img):
    # Get the dimensions of the image
    depth, height, width = img.shape

    # Extract one slice from each plane
    sagittal_slice_index = depth // 2  # Middle sagittal slice
    coronal_slice_index = height // 2   # Middle coronal slice
    axial_slice_index = width // 2      # Middle axial slice

    # Extract slices
    sagittal_slice = img.numpy()[sagittal_slice_index, :, :]
    coronal_slice = img.numpy()[:, coronal_slice_index, :]
    axial_slice = img.numpy()[:, :, axial_slice_index]

    # Visualize each slice
    slices = {'sagittal': sagittal_slice, 'coronal': coronal_slice, 'axial': axial_slice}
    for plane, slice_to_display in slices.items():
        plt.imshow(slice_to_display, cmap='gray')
        plt.title(f'{plane.capitalize()} Slice')
        plt.axis('off')
        plt.show()

In [ ]:
# Define the root directory path
root_directory = '/content/drive/MyDrive/ML_CN_Data/ADNI'

In [ ]:
def process_and_convert_folders(directory, output_folder):
    # Check if the root directory exists
    if not os.path.exists(directory):
        print(f"Directory not found: {directory}")
        return

    # Loop through items in the current directory
    for item in os.listdir(directory):
        item_path = os.path.join(directory, item)  # Get the full path

        # If the item is a directory, recurse into it
        if os.path.isdir(item_path):
            print(f"Entering directory: {item_path}")
            process_and_convert_folders(item_path, output_folder)  # Recurse into the subdirectory

    # Check for directories containing .dcm files
    dicom_files = [os.path.join(directory, file) for file in os.listdir(directory) if file.endswith(".dcm")]

    if len(dicom_files) > 0:  # Process if at least one DICOM file is found
        print(f"Found directory with {len(dicom_files)} DICOM file(s): {directory}")
        try:
            # Ensure the output folder exists
            if not os.path.exists(output_folder):
                os.makedirs(output_folder)

            # Convert DICOM to NIfTI
            dicom2nifti.convert_dir.convert_directory(directory, output_folder, compression=True, reorient=True)
            print(f"Converted DICOM files in {directory} to NIfTI format.")
        except Exception as e:
            print(f"Error converting DICOM files in {directory}: {e}")
    else:
        print(f"No DICOM files found in directory: {directory}")

# Define the root directory and output folder
root_directory = '/content/drive/MyDrive/ML_CN_Data/ADNI'
output_folder = '/content/drive/MyDrive/ML_CN_Data/converted'

# Process the root directory
process_and_convert_folders(root_directory, output_folder)

Entering directory: /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206
Entering directory: /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/Calibration_Scan
Entering directory: /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/Calibration_Scan/2014-01-21_11_56_43.0
Entering directory: /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/Calibration_Scan/2014-01-21_11_56_43.0/I405661
Found directory with 82 DICOM file(s): /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/Calibration_Scan/2014-01-21_11_56_43.0/I405661


/usr/local/lib/python3.10/dist-packages/pydicom/valuerep.py:440: UserWarning: Invalid value for VR UI: '2.16.124.113543.6006.99.06936431575310827308'. Please see <https://dicom.nema.org/medical/dicom/current/output/html/part05.html#table_6.2-1> for allowed values for each VR.
  warn_and_log(msg)


Converted DICOM files in /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/Calibration_Scan/2014-01-21_11_56_43.0/I405661 to NIfTI format.
No DICOM files found in directory: /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/Calibration_Scan/2014-01-21_11_56_43.0
Entering directory: /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/Calibration_Scan/2013-02-20_12_49_59.0
Entering directory: /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/Calibration_Scan/2013-02-20_12_49_59.0/I360830
Found directory with 82 DICOM file(s): /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/Calibration_Scan/2013-02-20_12_49_59.0/I360830
Converted DICOM files in /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/Calibration_Scan/2013-02-20_12_49_59.0/I360830 to NIfTI format.
No DICOM files found in directory: /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/Calibration_Scan/2013-02-20_12_49_59.0
No DICOM files found in directory: /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/Calibration_Scan
Entering d

/usr/local/lib/python3.10/dist-packages/pydicom/valuerep.py:440: UserWarning: Invalid value for VR UI: '2.16.124.113543.6006.99.04265028264717049777'. Please see <https://dicom.nema.org/medical/dicom/current/output/html/part05.html#table_6.2-1> for allowed values for each VR.
  warn_and_log(msg)


Converted DICOM files in /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/3-plane_localizer/2009-02-12_11_24_16.0/I135848 to NIfTI format.
Entering directory: /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/3-plane_localizer/2009-02-12_11_24_16.0/I135846
Found directory with 5 DICOM file(s): /content/drive/MyDrive/ML_CN_Data/ADNI/007_S_1206/3-plane_localizer/2009-02-12_11_24_16.0/I135846


...

Converted DICOM files in /content/drive/MyDrive/ML_CN_Data/ADNI/941_S_1203/localizer/2010-03-27_15_20_43.0/I171273 to NIfTI format.
Entering directory: /content/drive/MyDrive/ML_CN_Data/ADNI/941_S_1203/localizer/2010-03-27_15_20_43.0/I171271
Found directory with 1 DICOM file(s): /content/drive/MyDrive/ML_CN_Data/ADNI/941_S_1203/localizer/2010-03-27_15_20_43.0/I171271


Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/dicom2nifti/convert_dir.py", line 86, in convert_directory
    convert_dicom.dicom_array_to_nifti(dicom_input, nifti_file, reorient)
  File "/usr/local/lib/python3.10/dist-packages/dicom2nifti/convert_dicom.py", line 121, in dicom_array_to_nifti
    results = convert_siemens.dicom_to_nifti(dicom_list, output_file)
  File "/usr/local/lib/python3.10/dist-packages/dicom2nifti/convert_siemens.py", line 79, in dicom_to_nifti
    return convert_generic.dicom_to_nifti(dicom_input, output_file)
  File "/usr/local/lib/python3.10/dist-packages/dicom2nifti/convert_generic.py", line 230, in dicom_to_nifti
    common.validate_slicecount(dicom_input)
  File "/usr/local/lib/python3.10/dist-packages/dicom2nifti/common.py", line 1024, in validate_slicecount
    raise ConversionValidationError('TOO_FEW_SLICES/LOCALIZER')
dicom2nifti.exceptions.ConversionValidationError: TOO_FEW_SLICES/LOCALIZER


Converted DICOM files in /content/drive/MyDrive/ML_CN_Data/ADNI/941_S_1203/localizer/2010-03-27_15_20_43.0/I171271 to NIfTI format.
Entering directory: /content/drive/MyDrive/ML_CN_Data/ADNI/941_S_1203/localizer/2010-03-27_15_20_43.0/I171269
Found directory with 1 DICOM file(s): /content/drive/MyDrive/ML_CN_Data/ADNI/941_S_1203/localizer/2010-03-27_15_20_43.0/I171269


Converted DICOM files in /content/drive/MyDrive/ML_CN_Data/ADNI/941_S_1203/localizer/2010-03-27_15_20_43.0/I171269 to NIfTI format.
No DICOM files found in directory: /content/drive/MyDrive/ML_CN_Data/ADNI/941_S_1203/localizer/2010-03-27_15_20_43.0
No DICOM files found in directory: /content/drive/MyDrive/ML_CN_Data/ADNI/941_S_1203/localizer
No DICOM files found in directory: /content/drive/MyDrive/ML_CN_Data/ADNI/941_S_1203
No DICOM files found in directory: /content/drive/MyDrive/ML_CN_Data/ADNI


Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/dicom2nifti/convert_dir.py", line 86, in convert_directory
    convert_dicom.dicom_array_to_nifti(dicom_input, nifti_file, reorient)
  File "/usr/local/lib/python3.10/dist-packages/dicom2nifti/convert_dicom.py", line 121, in dicom_array_to_nifti
    results = convert_siemens.dicom_to_nifti(dicom_list, output_file)
  File "/usr/local/lib/python3.10/dist-packages/dicom2nifti/convert_siemens.py", line 79, in dicom_to_nifti
    return convert_generic.dicom_to_nifti(dicom_input, output_file)
  File "/usr/local/lib/python3.10/dist-packages/dicom2nifti/convert_generic.py", line 230, in dicom_to_nifti
    common.validate_slicecount(dicom_input)
  File "/usr/local/lib/python3.10/dist-packages/dicom2nifti/common.py", line 1024, in validate_slicecount
    raise ConversionValidationError('TOO_FEW_SLICES/LOCALIZER')
dicom2nifti.exceptions.ConversionValidationError: TOO_FEW_SLICES/LOCALIZER


In [ ]:
import os
import ants  # Ensure that the ANTs library is imported

# Define the root directory
root_directory = r'/content/mydrive/MyDrive/ML_Data/3D_datasets/CN_ADNI'
saved_directory = r"/content/mydrive/MyDrive/ML_Data/CN/extensive_preprocessed"

count = 0

def apply_pipeline(gz_path):
    # Extract filename without extension
    filename = os.path.basename(gz_path).replace(".gz", "")

    # Load, preprocess, and save the file
    try:
        # Step 1: Load images
        img_MRI_resampled, img_template_resampled, brain_mask_image = loading_ims(
            img=gz_path,
            template="MNI152_T1_1mm.nii",
            brain_mask="MNI152_T1_1mm_Brain_Mask.nii"
        )

        # Step 2: Registration
        aligned_image = regestration(img_MRI_resampled, img_template_resampled)

        # Step 3: Brain Masking
        brain_only_image = brain_masking(aligned_image, brain_mask_image)

        # Step 4: Winsorizing and Bias Field Correction
        preprocessed_image = winsorizing_biasfield(brain_only_image)

        #step 5:

        # Save the preprocessed image
        save_path = os.path.join(saved_directory, f"{filename}_preprocessed.nii")
        ants.image_write(preprocessed_image, save_path)
        print(f"Saved preprocessed image: {save_path}")

    except Exception as e:
        print(f"Error processing {gz_path}: {e}")

# Recursive function to navigate directories and process .dcm files
def process_folders(directory):
    global count  # Declare `count` as global to modify it inside the function
    # Loop through items in the current directory
    for item in os.listdir(directory):
        item_path = os.path.join(directory, item)  # Get the full path

        # Check if the item is a directory
        if os.path.isdir(item_path):
            print(f"Entering directory: {item_path}")
            process_folders(item_path)  # Recurse into the directory

        # If the item is not a directory, check for nifiti files
        elif os.path.isfile(item_path) and item_path.endswith('.nii'):
            print(f"Processing file: {item_path}")
            apply_pipeline(item_path)  # Apply the pipeline and save results
            count += 1  # Increment the counter

# Start processing from the root directory
process_folders(root_directory)
print('Number of images preprocessed:', count)

FileNotFoundError: [Errno 2] No such file or directory: '/content/mydrive/MyDrive/ML_Data/CN/CN_ADNI'

In [ ]:
# Global counter for processed images
count = 0

# Function to save one slice from each plane
def save_slices(img, output_folder, filename):
    # Get the dimensions of the image
    depth, height, width = img.shape

    # Extract one slice from each plane
    sagittal_slice_index = depth // 2  # Middle sagittal slice
    coronal_slice_index = height // 2   # Middle coronal slice
    axial_slice_index = width // 2      # Middle axial slice

    # Extract slices
    sagittal_slice = img.numpy()[sagittal_slice_index, :, :]
    coronal_slice = img.numpy()[:, coronal_slice_index, :]
    axial_slice = img.numpy()[:, :, axial_slice_index]

    # Save each slice as a .png file
    slices = {'sagittal': sagittal_slice, 'coronal': coronal_slice, 'axial': axial_slice}
    for plane, slice_to_save in slices.items():
        output_path = os.path.join(output_folder, f"{filename}_{plane}_slice.png")
        plt.imsave(output_path, slice_to_save, cmap='gray')
        print(f"{plane.capitalize()} slice saved at: {output_path}")

# Recursive function to navigate directories and process .nii files
def process_folders(directory, output_folder):
    global count  # Declare `count` as global to modify it inside the function
    # Loop through items in the current directory
    for item in os.listdir(directory):
        item_path = os.path.join(directory, item)  # Get the full path

        # Check if the item is a directory
        #if os.path.isdir(item_path):
            #print(f"Entering directory: {item_path}")
            #process_folders(item_path, output_folder)  # Recurse into the directory

        # If the item is not a directory, check for .nii files
        if os.path.isfile(item_path) and item_path.endswith('.nii'):
            print(f"Processing file: {item_path}")
            # Load the 3D image
            img = ants.image_read(item_path)

            # Prepare output filename (without extension)
            filename = os.path.splitext(os.path.basename(item_path))[0]

            # Save the slices
            save_slices(img, output_folder, filename)
            count += 1  # Increment the counter


# Define the root directory and output folder
root_directory = r'/content/Shareddrive/Shareddrives/ML_Data/3D_datasets/MCI/Preprocessed'
output_folder = r'/content/Shareddrive/Shareddrives/ML_Data/2D_datasets/MCI'

# Create output folder if it doesn't exist
os.makedirs(output_folder, exist_ok=True)

# Start processing from the root directory
process_folders(root_directory, output_folder)
print('Number of images sliced:', count)

Processing file: /content/Shareddrive/Shareddrives/ML_Data/3D_datasets/MCI/Preprocessed/ADNI_005_S_0324_MR_MPR-R__GradWarp__B1_Correction__N3_Br_20080430143333279_S49114_I104356.nii
Sagittal slice saved at: /content/Shareddrive/Shareddrives/ML_Data/2D_datasets/MCI/ADNI_005_S_0324_MR_MPR-R__GradWarp__B1_Correction__N3_Br_20080430143333279_S49114_I104356_sagittal_slice.png
Coronal slice saved at: /content/Shareddrive/Shareddrives/ML_Data/2D_datasets/MCI/ADNI_005_S_0324_MR_MPR-R__GradWarp__B1_Correction__N3_Br_20080430143333279_S49114_I104356_coronal_slice.png
Axial slice saved at: /content/Shareddrive/Shareddrives/ML_Data/2D_datasets/MCI/ADNI_005_S_0324_MR_MPR-R__GradWarp__B1_Correction__N3_Br_20080430143333279_S49114_I104356_axial_slice.png
Processing file: /content/Shareddrive/Shareddrives/ML_Data/3D_datasets/MCI/Preprocessed/ADNI_005_S_0324_MR_MPR-R__GradWarp__B1_Correction__N3_Br_20061212171807772_S12599_I32892.nii
